In [1]:
require 'redis'
require 'date'
require 'descriptive_statistics'

redis = Redis.new(host: "redis", port: 6379, db: 0)
class String

  def to_table_name
    
    self.gsub(/\W/, '')
  end

end

class Date
  def granule(granularity)
    granularities = [:year, :month, :day]
    idx =  granularities.index(granularity)
    granularities[0..idx].map{|g| eval "self.#{g}" }
  end
end

class Array

  def to_dot(filename = 'digraph.dot')
     File.open(filename, 'w') do |f|
       f.puts "digraph {"
       self.map{|e| f.puts "#{e[0]} -> #{e[1]};"}
       f.puts "}"
     end
  end

  def <(array)
    self.each_with_index do |i, idx|
      if i < array[idx] then  return true end
      if i > array[idx] then  return false end
    end
    return false
  end

  def entropy(params = {})
    p = {min: self.min, sup: self.max + 1}.merge(params)
    min, sup = p[:min], p[:sup]
    #if sup == min + 1 then return 0.0 end
    values, total = self.uniq, self.size.to_f
    if values.size <= 1 then return 0.0 end
    if total < 2 then return 0.0 end
    (values.map{|v| p = self.select{|i|i == v}.size.to_f / total; - (p * Math.log2(p))}.inject(:+))/Math.log2([2,sup - min].max)
  end

  def entropy2(params = {})
    p = {min: self.min, sup: self.max + 1}.merge(params)
    min, sup = p[:min], p[:sup]
    #if sup == min + 1 then return 0.0 end
    values, total = self.uniq, self.size.to_f
    if values.size <= 1 then return 0.0 end
    if total < 2 then return 0.0 end
    (values.map{|v| p = self.select{|i|i == v}.size.to_f / total; - (p * Math.log2(p)/Math.log2(self.uniq.size))}.inject(:+))  
  end
      
  def entropy_dn(params = {})
    p = {min: self.min, sup: self.max + 1}.merge(params)
    min, sup = p[:min], p[:sup]
    #if sup == min + 1 then return 0.0 end
    values, total = self.uniq, self.size.to_f
    if values.size <= 1 then return 0.0 end
    if total < 2 then return 0.0 end
    (values.map{|v| p = self.select{|i|i == v}.size.to_f / total; - (p * Math.log2(p))}.inject(:+))  
  end
      
  def devstd()
    m = self.mean
    sum = 0.0
    self.each {|v| sum += (v-m)**2 }
    Math.sqrt(sum/self.size)
  end
      
  #uso questa    
  def devstd_frel()
    m = self.mean
    sum = 0.0
    freq = Hash.new(0)
    self.each { |x| freq[x] += 1 }
    self.each {|v| sum += (v-m)**2 *freq[v]/freq.size }
    Math.sqrt(sum/self.size)
  end

  def devstd_fasb()
    m = self.mean
    sum = 0.0
    freq = Hash.new(0)
    self.each { |x| freq[x] += 1 }
    self.each {|v| sum += (v-m)**2 *freq[v]}
    Math.sqrt(sum/self.size)
  end
      
  def myVariance()
    m = self.mean
    sum = 0.0
    self.each {|v| sum += (v-m)**2 }
    Math.sqrt(sum/self.size)
  end
      
  def myVariance_frel()
    m = self.mean
    sum = 0.0
    freq = Hash.new(0)
    self.each { |x| freq[x] += 1 }
    self.each {|v| sum += (v-m)**2 *freq[v]/freq.size }
    Math.sqrt(sum/self.size)
  end

  def myVariance_fasb()
    m = self.mean
    sum = 0.0
    freq = Hash.new(0)
    self.each { |x| freq[x] += 1 }
    self.each {|v| sum += (v-m)**2 *freq[v]}
    Math.sqrt(sum/self.size)
  end
      
  def minimal_intervals(min_cases, zeroes)   
  intervals = []
  (0..size - 1).each do |i|
    found = nil
    if i == 0 || self[i - 1] == 0
      (i..size - 1).each{|j|
        if self[i..j].select{|item| item == 0}.size > zeroes then break end
        if self[i..j].sum == min_cases
          if j == size - 1 || self[j + 1] == 0
            found = j
            break
          end
        else  
          if self[i..j].sum > min_cases then break end
        end  
      }
    end
    if found
      intervals.push [i, found]
    end  
  end
  intervals    
  end   
    
    
end
      
      
def split(params = {})
  p = { epsilon: 0.7, verbose: false, use_weights: false }.merge(params)
  epsilon, series  = p[:epsilon], signal_series(p)
  total_sd, max_value = series.standard_deviation, series.max + 1
  total_ent= series.entropy
  total_sd_f = series.devstd_frel
  total_mean = series.mean
  n= series.sum
  # v1
  #a = -0.2       b = 0.2
  #delta = -0.2 + (((n-1)*0.4)/11359.0)
  #epsilon = epsilon1+ delta

  #v2
  if n <= 13
     epsilon= 0.6
  elsif n > 13  and n <= 25
     epsilon= 0.5
  elsif n > 25  and n <= 50
     epsilon= 0.3  
  elsif n > 50  and n <= 120
     epsilon= 0.2
  else
     epsilon= 0.1
  end
  
  weights = {}

  #puts "n: #{n}"
  #puts "epsilon1: #{epsilon1}"
  #puts "delta: #{delta}"
  #puts "epsilon: #{epsilon}"

  #puts "Series: #{series}"
  #puts "Max value: #{max_value}"
  #puts "total sd: #{total_sd}"
  #puts "Total entropy: #{total_ent}"
  if p[:verbose] then puts "#{Time.now}: starting split drug: #{p[:drug]} adr:  #{p[:adr]} " end
  if p[:verbose]
    puts "#{Time.now}: series"
    series.each{|s| puts s}
  end
 edges = (0..series.size - 1).to_a.select { |i|
    series_values =  series[0..i].map{|j| j[1]}
    weights[[0,i + 1]] = series_values.mean > 0 ? (series_values.devstd_frel / series_values.mean) : 0
    if series_values.mean > 0
      (series_values.devstd_frel / series_values.mean) <= (total_sd_f / total_mean) * epsilon
     else 
       true
    end
  }.map{|i| [0,i + 1]}
  edges += (0..series.size - 1).to_a.select { |i|
    series_values =  series[i..series.size - 1].map{|j| j[1]}
    weights[[i + 1, series.size + 1]] = series_values.mean > 0 ? (series_values.devstd_frel / series_values.mean) : 0 # SETTA
   if series_values.mean > 0
      (series_values.devstd_frel / series_values.mean) <= (total_sd_f / total_mean) * epsilon
     else 
       true
    end
  }.map{|i| [i + 1, series.size + 1]}
  edges +=  (0..series.size - 1).to_a.product((0..series.size - 1).to_a).select{|i| i[0] < i[1]}.select{|i|
    series_values =  series[i[0]..i[1] - 1].map{|j| j[1]}
    weights[[i[0] + 1, i[1] + 1 ]] = series_values.mean > 0 ? (series_values.devstd_frel / series_values.mean) : 0 # SETTA
    if series_values.mean > 0
      (series_values.devstd_frel / series_values.mean) <= (total_sd_f / total_mean) * epsilon
     else 
       true
    end
  }.map{|i| [i[0] + 1, i[1] + 1 ]}
    
    #puts "series #{series}"
    #puts "minimal_intervals: #{series.minimal_intervals(3,0)} \n\n\n"
    #edges += series.minimal_intervals(3,4)


   p[:use_weights] ? weighted_shp(edges, weights) : shp(edges)
end

def shp(edges)
  t = edges.flatten.max
  shp = (0..t).to_a.map{|_| Float::INFINITY}; shp[0] = 0
  pre = (0..t).to_a.map{|_| nil}
  edges.sort{|a,b| a <=> b}.each{|e| if shp[e[1]] > shp[e[0]] + 1 then shp[e[1]] = shp[e[0]] + 1; pre[e[1]] = e[0] end}
  r = [t]; while !pre[r[-1]].nil? do  r.push(pre[r[-1]]) end
  r.reverse
end          

def weighted_shp(edges, weights)
  t = edges.flatten.max
  shp = (0..t).to_a.map{|_| Float::INFINITY}; shp[0] = 0
  pre = (0..t).to_a.map{|_| nil}
  edges.sort{|a,b| a <=> b}.each{|e| if shp[e[1]] > shp[e[0]] + weights[e] then shp[e[1]] = shp[e[0]] + weights[e]; pre[e[1]] = e[0] end}
  r = [t]; while !pre[r[-1]].nil? do  r.push(pre[r[-1]]) end
  r.reverse
end       
  
def init_temporal_values(params = {})
  (params[:start_date]..params[:end_date]).to_a.map{|ts| ts.granule(params[:granularity]) }.uniq
end  
  
  
SOC_REDIS = redis  

def signal_series(params = {})
  p = {
       redis: SOC_REDIS,
       adr_level: :soc,
       granularity: :month,
       vts:  [2008, 1],
       vte: [2017,12]
  }.merge(params)
  
  # drug, adr, is_soc, granularity  = p[:drug], p[:adr], p[:soc?], p[:granularity]
  tv = init_temporal_values(start_date: Date.new(p[:vts][0],p[:vts][1],1), 
                       end_date: Date.new(p[:vte][0],p[:vte][1],1), 
                       granularity: :month)
  r = tv.map do |y,m|
                          key = {incremental: false, year: y, month: m, drug: p[:drug], p[:adr_level] => p[:adr] }  
                          v =  p[:redis].get(key)
                          v.nil? ? 0 :  v.to_i
                       end
  p[:granularity] == :year ?  r.each_slice(12).to_a.map{|i| i.reduce(:+)} : r
  
end

:signal_series

In [2]:
#portato incremental a false, verificare se cambiano i res
pairs = redis.keys({incremental: true, year: 2017, month: 12, drug: "*", soc: "*"}.to_s); nil
pairs = pairs.map{|p| h = (eval p); {drug: h[:drug], adr: h[:soc]} }.uniq


[{:drug=>"LEVOCETIRIZINA DICLORIDRATO", :adr=>"General disorders and administration site conditions"}, {:drug=>"CALCIO FOLINATO/CIANOCOBALAMINA", :adr=>"Investigations"}, {:drug=>"MIVACURIO CLORURO", :adr=>"Injury, poisoning and procedural complications"}, {:drug=>"CEFACLOR MONOIDRATO", :adr=>"Eye disorders"}, {:drug=>"MIRTAZAPINA", :adr=>"Surgical and medical procedures"}, {:drug=>"DASATINIB", :adr=>"Nervous system disorders"}, {:drug=>"ELBASVIR/GRAZOPREVIR", :adr=>"Injury, poisoning and procedural complications"}, {:drug=>"DOXORUBICINA LIPOSOMIALE PEGILATA", :adr=>"Hepatobiliary disorders"}, {:drug=>"ALFUZOSINA", :adr=>"Skin and subcutaneous tissue disorders"}, {:drug=>"OMBITASVIR", :adr=>"Cardiac disorders"}, {:drug=>"IOMEPROLO", :adr=>"Psychiatric disorders"}, {:drug=>"ENFUVIRTIDE", :adr=>"Immune system disorders"}, {:drug=>"CRIZOTINIB", :adr=>"General disorders and administration site conditions"}, {:drug=>"VACCINO TETANICO ADSORBITO", :adr=>"General disorders and administration s

In [60]:
#print to stdout
pairs.each{|p| 
  puts p
  puts split(p.merge({granularity: :month, verbose: false}))
  }

{:drug=>"POTASSIO CLORURO", :adr=>"Metabolism and nutrition disorders"}
n: 226
epsilon: 0.2
[0, 1, 16, 17, 26, 27, 40, 41, 43, 46, 47, 48, 49, 50, 53, 54, 59, 60, 63, 64, 65, 67, 69, 70, 71, 72, 75, 76, 78, 79, 80, 82, 84, 85, 88, 89, 91, 92, 93, 94, 100, 101, 102, 103, 104, 105, 108, 109, 110, 111, 112, 114, 118, 121]
{:drug=>"DEQUALINIO CLORURO", :adr=>"Renal and urinary disorders"}
n: 1
epsilon: 0.05
[0, 1, 121]
{:drug=>"ACIDO ALENDRONICO SALE SODICO", :adr=>"Investigations"}
n: 18
epsilon: 0.1
[0, 1, 29, 30, 102, 103, 121]
{:drug=>"OMBITASVIR", :adr=>"Renal and urinary disorders"}
n: 4
epsilon: 0.05
[0, 1, 121]
{:drug=>"CLORMADINONE ACETATO/ETINILESTRADIOLO", :adr=>"Cardiac disorders"}
n: 1
epsilon: 0.05
[0, 1, 121]
{:drug=>"BUDESONIDE/FORMOTEROLO FUMARATO DIIDRATO", :adr=>"Metabolism and nutrition disorders"}
n: 23
epsilon: 0.1
[0, 1, 14, 15, 43, 44, 47, 48, 82, 83, 85, 86, 121]
{:drug=>"COBIMETINIB EMIFUMARATO", :adr=>"Eye disorders"}
n: 5
epsilon: 0.05
[0, 1, 112, 113, 121]
{:dr

Interrupt: 

In [ ]:
#write to file
pairs.each{|p| 
  split=split(p.merge({granularity: :month, verbose: false}))
  s= split.map { |i| i.to_s }.join(",")
  File.write("split_DinEps-v4_chi5_ci5.txt", p[:drug]+"\t"+p[:adr]+"\t"+s+"\n", mode: "a")
}

[{:drug=>"LEVOCETIRIZINA DICLORIDRATO", :adr=>"General disorders and administration site conditions"}, {:drug=>"CALCIO FOLINATO/CIANOCOBALAMINA", :adr=>"Investigations"}, {:drug=>"MIVACURIO CLORURO", :adr=>"Injury, poisoning and procedural complications"}, {:drug=>"CEFACLOR MONOIDRATO", :adr=>"Eye disorders"}, {:drug=>"MIRTAZAPINA", :adr=>"Surgical and medical procedures"}, {:drug=>"DASATINIB", :adr=>"Nervous system disorders"}, {:drug=>"ELBASVIR/GRAZOPREVIR", :adr=>"Injury, poisoning and procedural complications"}, {:drug=>"DOXORUBICINA LIPOSOMIALE PEGILATA", :adr=>"Hepatobiliary disorders"}, {:drug=>"ALFUZOSINA", :adr=>"Skin and subcutaneous tissue disorders"}, {:drug=>"OMBITASVIR", :adr=>"Cardiac disorders"}, {:drug=>"IOMEPROLO", :adr=>"Psychiatric disorders"}, {:drug=>"ENFUVIRTIDE", :adr=>"Immune system disorders"}, {:drug=>"CRIZOTINIB", :adr=>"General disorders and administration site conditions"}, {:drug=>"VACCINO TETANICO ADSORBITO", :adr=>"General disorders and administration s

In [58]:
File.readlines('split_month_sigma01SAMPLE.txt').each do |line|
  array=line.strip.split("\t")
  pairs = { :drug => array[0], :soc => array[1] } 
  pairs = redis.keys({incremental: true, year: 2017, month: 12, drug: pairs[:drug].to_s, soc: pairs[:soc].to_s}.to_s); nil
  pairs = pairs.map{|p| h = (eval p); {drug: h[:drug], adr: h[:soc]} }.uniq
  pairs.each { |p|
    puts "\nNew association"
    puts p
    puts split(p.merge({granularity: :month, verbose: false}))
    File.write("example.txt", p[:drug]+"\t"+p[:adr]+"\t"+split(p.merge({granularity: :month, verbose: false})).to_s+"\n", mode: "a")
}
end


New association
{:drug=>"ACICLOVIR", :adr=>"Immune system disorders"}


TypeError: nil can't be coerced into Integer